In [1]:
import pandas as pd

In [2]:
# "source": "https://webstore.iec.ch/publication/68709",
# "seq_num": 1328,
# "domain": "",
# "id": "IEC 60050-102:2007/AMD3:2021",
# "year_public": "2021-03-23 07:00:00",
# "status": "Còn hiệu lực",
# "name_en": "Amendment 3 - International Electrotechnical Vocabulary (IEV) - Part 102: Mathematics - General concepts and linear algebra",
# "name_vn": ""

In [3]:
df1 = pd.read_excel("./data/Tiêu chuẩn (tcvn) 02112024.xlsx")
df1.head(1)

id        so_hieu  \
0  __export__.tcvn_12325_e44bff59  ISO 4054:1980   

                                       ten_tieng_anh  \
0  Couplers, loose spigots and base-plates for us...   

                                               mo_ta        nam_ban_hanh  \
0  Couplers, loose spigots and base-plates for us... 1980-04-01 07:00:00   

      status         phan_cap_ids loai_ids  \
0  Withdrawn  ISO -> 91 -> 91.220      ISO   

                                          duong_link  
0  https://www.iso.org/standard/9760.html?browse=ics

In [4]:
df1['page_content'] = df1[['ten_tieng_anh', 'mo_ta']].apply(lambda x: "{}\n\n{}".format(x[0],x[1]), axis=1)

/tmp/ipykernel_3206646/3214845764.py:1: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  df1['page_content'] = df1[['ten_tieng_anh', 'mo_ta']].apply(lambda x: "{}\n\n{}".format(x[0],x[1]), axis=1)


In [5]:
df1 = df1.drop(columns=['id'], axis=1)

In [6]:
df1.rename(columns={'so_hieu': 'id',
 'nam_ban_hanh': 'year_public',
 'Tổ chức': 'organization',
 'mo_ta': 'description',
 'status': 'status',
 'ten_tieng_anh': 'name_en',
 'duong_link':'link',
 'phan_cap_ids': 'branch'}, inplace=True)

In [7]:
df1.to_csv('./data/Tiêu chuẩn (tcvn) (3).csv', encoding='utf-8', index=False)

In [8]:
df1 = pd.read_csv("./data/Tiêu chuẩn (tcvn) (3).csv")

In [9]:
df1['year_public'] = df1['year_public'].astype(str)

In [10]:
dt = df1.to_dict('records')
dt

[{'id': 'ISO 4054:1980',
  'name_en': 'Couplers, loose spigots and base-plates for use in working scaffolds made of steel tubes — Requirements and test procedure',
  'description': 'Couplers, loose spigots and base-plates for use in working scaffolds made of steel tubes — Requirements and test procedure',
  'year_public': '1980-04-01 07:00:00',
  'status': 'Withdrawn',
  'branch': 'ISO -> 91 -> 91.220',
  'loai_ids': 'ISO',
  'link': 'https://www.iso.org/standard/9760.html?browse=ics',
  'page_content': 'Couplers, loose spigots and base-plates for use in working scaffolds made of steel tubes — Requirements and test procedure\n\nCouplers, loose spigots and base-plates for use in working scaffolds made of steel tubes — Requirements and test procedure'},
 {'id': 'ISO 4872:1978',
  'name_en': 'Acoustics — Measurement of airborne noise emitted by construction equipment intended for outdoor use — Method for determining compliance with noise limits',
  'description': 'Describes a procedure fo

In [11]:
import json
with open('./data/data_standard.json', 'w', encoding='utf-8') as json_file:
  json.dump({"data": dt}, json_file, ensure_ascii='True')

In [12]:
df2 = pd.read_csv("./data/Phan Cap (phan_cap) 18102024.csv", encoding='ISO-8859-1', sep=",")
df2.sample(5)

display_name       name        description  \
1759  ISO -> 81 -> 81.060 -> 81.060.30  81.060.30  Advanced ceramics   
423                                NaN        NaN                NaN   
939                                NaN        NaN                NaN   
912                          ISO -> 31         31        Electronics   
2077                               NaN        NaN                NaN   

                  parrent                          children  
1759  ISO -> 81 -> 81.060                               NaN  
423                   NaN  ISO -> 13 -> 13.030 -> 13.030.50  
939                   NaN               ISO -> 33 -> 33.180  
912                   ISO               ISO -> 31 -> 31.020  
2077                  NaN                        ITU-T -> I

<!-- TC_101 -->
<!-- encoding='ISO-8859-1' -->
<!-- encoding='latin-1' -->

In [17]:
from langchain_community.document_loaders import JSONLoader
# -*- coding: utf-8 -*-
from langchain_community.vectorstores import FAISS
from langchain.embeddings import OpenAIEmbeddings
import json

In [15]:

with open('./data/data_standard.json', 'r') as f:
    dx = json.load(f)
dx

{'data': [{'id': 'ISO 4054:1980',
   'name_en': 'Couplers, loose spigots and base-plates for use in working scaffolds made of steel tubes — Requirements and test procedure',
   'description': 'Couplers, loose spigots and base-plates for use in working scaffolds made of steel tubes — Requirements and test procedure',
   'year_public': '1980-04-01 07:00:00',
   'status': 'Withdrawn',
   'branch': 'ISO -> 91 -> 91.220',
   'loai_ids': 'ISO',
   'link': 'https://www.iso.org/standard/9760.html?browse=ics',
   'page_content': 'Couplers, loose spigots and base-plates for use in working scaffolds made of steel tubes — Requirements and test procedure\n\nCouplers, loose spigots and base-plates for use in working scaffolds made of steel tubes — Requirements and test procedure'},
  {'id': 'ISO 4872:1978',
   'name_en': 'Acoustics — Measurement of airborne noise emitted by construction equipment intended for outdoor use — Method for determining compliance with noise limits',
   'description': 'Desc

In [43]:
with open('./data_standard.json', 'w', encoding='utf-8') as json_file:
  json.dump(dx, json_file, ensure_ascii='True')

In [19]:
# Define the metadata extraction function.
def metadata_func(record: dict, metadata: dict) -> dict:

    if "source" in metadata:
        metadata["source"] = record.get("link")
    metadata["domain"] = record.get("loai_ids")
    metadata["description"] = record.get("description")
    metadata["id"] = record.get("id")
    metadata["branch"] = record.get("branch")
    metadata["year_public"] = record.get("year_public")
    metadata["status"] = record.get("status")
    metadata["name_en"] = record.get("name_en")
    # metadata["timestamp_ms"] = record.get("timestamp_ms")

    # if "source" in metadata:
    #     source = metadata["source"].split("/")
    #     source = source[source.index("langchain"):]
    #     metadata["source"] = "/".join(source)

    return metadata


loader = JSONLoader(
    file_path='./data/data_standard.json',
    jq_schema='.data[]',
    content_key="page_content",
    metadata_func=metadata_func
)

data = loader.load()
data

[Document(metadata={'source': 'https://www.iso.org/standard/9760.html?browse=ics', 'seq_num': 1, 'domain': 'ISO', 'description': 'Couplers, loose spigots and base-plates for use in working scaffolds made of steel tubes — Requirements and test procedure', 'id': 'ISO 4054:1980', 'branch': 'ISO -> 91 -> 91.220', 'year_public': '1980-04-01 07:00:00', 'status': 'Withdrawn', 'name_en': 'Couplers, loose spigots and base-plates for use in working scaffolds made of steel tubes — Requirements and test procedure'}, page_content='Couplers, loose spigots and base-plates for use in working scaffolds made of steel tubes — Requirements and test procedure\n\nCouplers, loose spigots and base-plates for use in working scaffolds made of steel tubes — Requirements and test procedure'),
 Document(metadata={'source': 'https://www.iso.org/standard/10856.html?browse=ics', 'seq_num': 2, 'domain': 'ISO', 'description': 'Describes a procedure for measuring the weighted sound pressure levels at prescribed micropho

In [27]:
data[0].metadata['year_public']

'1980-04-01 07:00:00'

In [28]:
import getpass
import os
os.environ["OPENAI_API_KEY"] = getpass.getpass()

from langchain_openai import OpenAIEmbeddings

embeddings = OpenAIEmbeddings()

In [30]:
# Embeding
embed_model = OpenAIEmbeddings()
db = FAISS.from_documents(data[:-1], embed_model)
vector_db_path = "./Chatbot_02112024/"
db.save_local(vector_db_path)

In [31]:
db = FAISS.load_local("./Chatbot_02112024/", embeddings=OpenAIEmbeddings(), allow_dangerous_deserialization = True)

In [32]:
num_documents = len(db.index_to_docstore_id)
print(f"Total number of documents: {num_documents}")

Total number of documents: 36051


In [32]:
query_vec = "standard involve in Machine Learning"
# output = db.similarity_search_by_vector(query_vec, k=2, score_threshold=0.2)
retrieve = db.as_retriever(
    search_type="similarity_score_threshold",
    search_kwargs={'score_threshold': 0.6, "fetch_k": num_documents, "k": num_documents},
)
output = retrieve.invoke(query_vec)
output

[Document(metadata={'source': 'https://www.iso.org/standard/81093.html?browse=ics', 'seq_num': 28452, 'domain': None, 'id': 'ISO/IEC 5259-4:2024', 'branch': 'ISO -> 35 -> 35.020', 'year_public': 'nan', 'status': 'Còn hiệu lực', 'name_en': 'Artificial intelligence — Data quality for analytics and machine learning (ML)', 'name_vn': None}, page_content='ISO ROOT\nInformation technology\nInformation technology (IT) in generalIncluding general aspects of IT equipment\nArtificial intelligence — Data quality for analytics and machine learning (ML)\n\nThis document establishes general common organizational approaches, regardless of the type, size or nature of the applying organization, to ensure data quality for training and evaluation in analytics and machine learning (ML). It includes guidance on the data quality process for:—supervised ML with regard to the labelling of data used for training ML systems, including common organizational approaches for training data labelling;—unsupervised ML

In [38]:
output[:10]

[Document(metadata={'source': 'https://www.iso.org/standard/81093.html?browse=ics', 'seq_num': 28452, 'domain': None, 'id': 'ISO/IEC 5259-4:2024', 'branch': 'ISO -> 35 -> 35.020', 'year_public': 'nan', 'status': 'Còn hiệu lực', 'name_en': 'Artificial intelligence — Data quality for analytics and machine learning (ML)', 'name_vn': None}, page_content='ISO ROOT\nInformation technology\nInformation technology (IT) in generalIncluding general aspects of IT equipment\nArtificial intelligence — Data quality for analytics and machine learning (ML)\n\nThis document establishes general common organizational approaches, regardless of the type, size or nature of the applying organization, to ensure data quality for training and evaluation in analytics and machine learning (ML). It includes guidance on the data quality process for:—supervised ML with regard to the labelling of data used for training ML systems, including common organizational approaches for training data labelling;—unsupervised ML

In [27]:
query_vec = "standard involve in Machine Learning"
# output = db.similarity_search_by_vector(query_vec, k=2, score_threshold=0.2)
results = db.similarity_search_with_score(
    query_vec, k=10,
)
results[0][0].metadata['year_public']

'NaT'

In [34]:
docs, scores = zip(*db.similarity_search_with_relevance_scores(query_vec, score_threshold=0.6, k=num_documents))

In [37]:
docs[:10]

(Document(metadata={'source': 'https://www.iso.org/standard/81093.html?browse=ics', 'seq_num': 28452, 'domain': None, 'id': 'ISO/IEC 5259-4:2024', 'branch': 'ISO -> 35 -> 35.020', 'year_public': 'nan', 'status': 'Còn hiệu lực', 'name_en': 'Artificial intelligence — Data quality for analytics and machine learning (ML)', 'name_vn': None}, page_content='ISO ROOT\nInformation technology\nInformation technology (IT) in generalIncluding general aspects of IT equipment\nArtificial intelligence — Data quality for analytics and machine learning (ML)\n\nThis document establishes general common organizational approaches, regardless of the type, size or nature of the applying organization, to ensure data quality for training and evaluation in analytics and machine learning (ML). It includes guidance on the data quality process for:—supervised ML with regard to the labelling of data used for training ML systems, including common organizational approaches for training data labelling;—unsupervised ML

In [22]:
x = output[0].to_json()
x

{'lc': 1,
 'type': 'constructor',
 'id': ['langchain', 'schema', 'document', 'Document'],
 'kwargs': {'metadata': {'source': 'https://www.iso.org/standard/81093.html?browse=ics',
   'seq_num': 28452,
   'domain': None,
   'id': 'ISO/IEC 5259-4:2024',
   'branch': 'ISO -> 35 -> 35.020',
   'year_public': 'NaT',
   'status': 'Còn hiệu lực',
   'name_en': 'Artificial intelligence — Data quality for analytics and machine learning (ML)',
   'name_vn': None},
  'page_content': 'ISO ROOT\nInformation technology\nInformation technology (IT) in generalIncluding general aspects of IT equipment\nArtificial intelligence — Data quality for analytics and machine learning (ML)\n\nThis document establishes general common organizational approaches, regardless of the type, size or nature of the applying organization, to ensure data quality for training and evaluation in analytics and machine learning (ML). It includes guidance on the data quality process for:—supervised ML with regard to the labelling o

In [10]:
output[0]

Document(metadata={'source': 'https://www.iso.org/standard/81093.html?browse=ics', 'seq_num': 28452, 'domain': None, 'id': 'ISO/IEC 5259-4:2024', 'branch': 'ISO -> 35 -> 35.020', 'year_public': 'NaT', 'status': 'Còn hiệu lực', 'name_en': 'Artificial intelligence — Data quality for analytics and machine learning (ML)', 'name_vn': None}, page_content='ISO ROOT\nInformation technology\nInformation technology (IT) in generalIncluding general aspects of IT equipment\nArtificial intelligence — Data quality for analytics and machine learning (ML)\n\nThis document establishes general common organizational approaches, regardless of the type, size or nature of the applying organization, to ensure data quality for training and evaluation in analytics and machine learning (ML). It includes guidance on the data quality process for:—supervised ML with regard to the labelling of data used for training ML systems, including common organizational approaches for training data labelling;—unsupervised ML;